# Cleaning the data

Transforming the data from a mongodb collection to a csv file 


In [1]:
import pymongo

# Connection to Mongo DB
try:
    conn=pymongo.MongoClient()
    print("connected")
except pymongo.errors.ConnectionFailure as e:
    print ("Could not connect to MongoDB: %s" % e )

db = conn["idealista"]
collection = db["house_data"]
urls = db["urls"]


connected


In [2]:
import pandas as pd
import math
import numpy as np
df = pd.DataFrame()

In [3]:
# Exploring the data

collection.find_one()

{'_id': ObjectId('5dece54c833639ed33008205'),
 'price': '173.000 €',
 'features': [' 35 m² ', ' 2 hab. '],
 'description': ' "En la zona peatonal del barrio de Sant Pere i Santa Caterina encontramos esta propiedad en la segunda planta del edificio antiguo, sin ascensor, típico de la zona. Se trata de un estudio reformado hace unos años con calidades apropiadas para las exigencias de la zona. El piso se vende amueblado tal y como está en las fotos. Puede ser interesante para su alquiler (alrededor de 850€/mes). Ubicado en pleno centro de Barcelona, con todos los servicios cerca, sin necesidad de tener el coche.Ubicado en la mejor y más buscada área del Born, esta obra se encuentra a pocos pasos de Arc de Triomf, Parc de la Ciutadella, muy bien comunicada con transporte público (tren, metro, autobuses)." ',
 'details_house': ['35 m² construidos',
  '2 habitaciones',
  '1 baño',
  'Construido en 1848'],
 'details_building': [' Aire acondicionado '],
 'energy_class': 'd',
 'address': [' ',

# Checking how to extract data 


In [13]:
# price

def getPrice(doc,l):
    price = doc["price"]
    price = price.replace("€","").replace(".","")
    price = price.strip()
    try:
        price = int(price)
    except:
        #print(price)
        price = 0
    l.append(price)
    
cursor = collection.find({},{"price":1})
prices = []
for doc in cursor:
    getPrice(doc,prices)

print(len(prices))
print("done")
    

15436
done


In [5]:
# features
def append_zero(*lists):
    for list in lists:
        list.append(0)
        
f =set()
m2 = []
ascensor = []
exterior = []
planta = []
garaje = []
habs = []

def getFeatures(doc,m2,ascensor,exterior,planta,garaje,habs,f):
    append_zero(ascensor,exterior,garaje,planta,habs)
    last_idx = len(ascensor)-1
    for feature in doc["features"]:        
        if "m²" in feature:
            m = feature.strip()
            m = feature.split(" ")[1] 
            m = m.strip()
            m = int(math.floor(float(m)))
            m2.append(m)
            continue
        if "con ascensor" in feature:
            ascensor[last_idx] = 1
        if "exterior" in feature:
            exterior[last_idx]=1
        if "ª planta" in feature:
            p = feature.split("ª planta")
            p = int(p[0])
            planta[last_idx] = p
            continue        
        if "Garaje incluido" in feature:
            garaje[last_idx] = 1
            continue
        if "hab" in feature:
            h = feature.strip()
            h = feature.split(" ")[1]
            h = int(h)
            habs[last_idx] = h
            continue
        skip_it = False
        for skip in [ "Bajo","Entreplanta","exterior","interior","ascensor","Garaje"]:
            if skip in feature:
                skip_it = True
                break
        if skip_it: continue
        if f is not None: f.add(feature) # untreated feature
        
cursor = collection.find({},{"features":1})
for doc in cursor:
    getFeatures(doc,m2,ascensor,exterior,planta,garaje,habs,f)
#df["price"]=l
f
    

{'opc.'}

In [9]:
len(m2),len(planta),len(ascensor),len(exterior),len(garaje),len(habs)

(15436, 15436, 15436, 15436, 15436, 15436)

In [6]:
# details house


dh = {}
construido_en = []
banos = []
calefacion_central = []
calefacion_individual = []
es_casa = []
orientacion_sur = []
orientacion_oeste = []
orientacion_este = []
orientacion_norte = []
buen_estado = []
obra_nueva = []
movilidad_reducida = []
balcon = []
armarios = []
terraza = []
trastero = []

def set_to_one(feature,*l_tests):
    for text,var in l_tests:
        if text in feature:
            if var:
                var[len(var)-1] = 1
            return True
    return False

def getDetailsHouse(doc,construido_en,banos,calefacion_central,calefacion_individual,es_casa,orientacion_sur,
                        orientacion_oeste,orientacion_este,orientacion_norte,buen_estado,obra_nueva,
                        movilidad_reducida,balcon,armarios,terraza,trastero,dh):
    
    append_zero(terraza, trastero, armarios,balcon,buen_estado,obra_nueva,
                orientacion_sur, orientacion_oeste, orientacion_este,
                movilidad_reducida,orientacion_norte, calefacion_central, calefacion_individual,es_casa)
    banos.append(1)
    construido_en.append(np.nan)
    last_idx = len(construido_en)-1
    for feature in doc["details_house"]:        
        if "m²" in feature:
            continue            
        if "Construido en " in feature:
            construido_en[last_idx] = int(feature.split(" en ")[1])
            continue
        if "baño" in feature:
            try: 
                banos[last_idx] = int(feature.split("baño")[0])
            except:
                banos[last_idx] = 0
            continue
        if "Casa" in feature or "Chalet" in feature or "Finca" in feature:
                es_casa[last_idx] = 1
                continue        
        if "Orientación" in feature:
            if "norte" in feature:
                orientacion_norte[last_idx] = 1           
            if "sur" in feature:
                orientacion_sur[last_idx] = 1
            if "oeste" in feature:
                orientacion_oeste[last_idx] = 1           
            if "este" in feature:
                orientacion_este[last_idx] = 1
            continue
            
        if set_to_one(feature, ("Calefacción central",calefacion_central),
                        ("Calefacción individual", calefacion_individual),
                     ("habitaci",None),("obra nueva",obra_nueva),
                      ("buen estado", buen_estado),
                      ("movilidad reducida" , movilidad_reducida ) ,
                      ("Balcón", balcon ), ("Armarios",armarios), 
                      ("Terraza",terraza), ("Trastero",trastero) ):
            continue
            
        skip_it = False
        for skip in [ "planta","Certificación energética","garaje","ascensor","Garaje",
                     "calefacción","Segunda mano"]:
            if skip in feature:
                skip_it = True
                break
        if skip_it: continue
        if dh is not None: dh[feature] = dh.get(feature,0) + 1 # untreated feature
        
        
cursor = collection.find({},{"details_house":1})
for doc in cursor:
    getDetailsHouse(doc,construido_en,banos,calefacion_central,calefacion_individual,es_casa,
                   orientacion_sur,orientacion_oeste,orientacion_este,orientacion_norte,buen_estado,
                   obra_nueva,movilidad_reducida,balcon,armarios,terraza,trastero,dh) 
    

dh

{'Chimenea': 1}

In [7]:
#details building

db = {}
jardin = []
piscina = []
aire = []

def getDetailsBuilding(doc,jardin,piscina,aire,db):
    append_zero(piscina,jardin,aire)
    last_idx = len(piscina)
    for feature in doc["details_building"]:        
        if "Planta" in feature:
            continue     
            
        if set_to_one(feature, ("Piscina", piscina), ("Aire", aire),("Jardín",jardin),("Zonas verdes",jardin) ):
            continue
            
        skip_it = False
        for skip in [ "Bajo","ótano","ascensor","Entreplanta","exterior","interior"]:
            if skip in feature:
                skip_it = True
                break
        if skip_it: continue
        if db is not None: db[feature] = db.get(feature,0) + 1 # untreated feature


cursor = collection.find({},{"details_building":1})
for doc in cursor:
    getDetailsBuilding(doc,jardin,piscina,aire,db)

db

{}

In [8]:
len(jardin),len(piscina),len(aire),sum(jardin),sum(piscina),sum(aire)

(15436, 15436, 15436, 847, 733, 8441)

In [11]:
#'energy_class'

def getEnergyClass(doc,energy_class,ec):
    val = doc['energy_class']
    if ec is not None: ec[val] = ec.get(val,0)+1 
    if val=="": 
        val = np.nan
    else:
        val = "abcdefg".find(val)
    energy_class.append(val)

ec= {}
energy_class = []

cursor = collection.find({},{'energy_class':1})
for doc in cursor:
    getEnergyClass(doc,energy_class,ec)
    
    
ec
len(energy_class)

15436

In [33]:
cursor = collection.find({},{'address':1})
set_barrios = set()
set_distritos = set()
# get a list of all barrios and distritos in the collection
distritos = []

def getDistrito(doc,set_barrios,set_distritos,distritos):
    #print(doc["address"][1])
    barrio = doc["address"][1].strip()
    distrito = doc["address"][2].strip()
    if barrio:
        if "Barrio" not in barrio and "Urb" not in barrio:
            print(barrio)
        if "-" in barrio: barrio = barrio.split("-")[0].strip()
        barrio = " ".join(barrio.split(" ")[1:]).strip()
        #print(barrio)
        set_barrios.add(barrio)
    if distrito:
        distrito = " ".join(distrito.split(" ")[1:]).strip()
        set_distritos.add(distrito)
        distritos.append(distrito)
        
for doc in cursor:
    getDistrito(doc,set_barrios,set_distritos,distritos)

dic_distritos = {}
l_distritos = list(set_distritos)
for idx in range(len(l_distritos)):
    dic_distritos["distrito_"+str(idx)]=[]

for distrito in distritos:
    idx = l_distritos.index(distrito)
    for i in range(len(l_distritos)):
        name = "distrito_"+str(i)
        val = 1 if i==idx else 0
        dic_distritos[name].append(val)
def makeListDistritos(distrito,l):
    result = [0]*len(l)
    result[ l.index(distrito)] = 1
    return result

for i,distrito in enumerate(distritos):
    distritos[i] = makeListDistritos(distrito,l_distritos)
print(len(set_barrios),len(set_distritos))
print(len(distritos))
#set_distritos


446 69
15436


In [42]:
print(dic_distritos.keys())
sum(dic_distritos["distrito_24"])
l=[ sum(dic_distritos[key]) for key in dic_distritos.keys()]
print(sum(l))
print(l)


dict_keys(['distrito_0', 'distrito_1', 'distrito_2', 'distrito_3', 'distrito_4', 'distrito_5', 'distrito_6', 'distrito_7', 'distrito_8', 'distrito_9', 'distrito_10', 'distrito_11', 'distrito_12', 'distrito_13', 'distrito_14', 'distrito_15', 'distrito_16', 'distrito_17', 'distrito_18', 'distrito_19', 'distrito_20', 'distrito_21', 'distrito_22', 'distrito_23', 'distrito_24', 'distrito_25', 'distrito_26', 'distrito_27', 'distrito_28', 'distrito_29', 'distrito_30', 'distrito_31', 'distrito_32', 'distrito_33', 'distrito_34', 'distrito_35', 'distrito_36', 'distrito_37', 'distrito_38', 'distrito_39', 'distrito_40', 'distrito_41', 'distrito_42', 'distrito_43', 'distrito_44', 'distrito_45', 'distrito_46', 'distrito_47', 'distrito_48', 'distrito_49', 'distrito_50', 'distrito_51', 'distrito_52', 'distrito_53', 'distrito_54', 'distrito_55', 'distrito_56', 'distrito_57', 'distrito_58', 'distrito_59', 'distrito_60', 'distrito_61', 'distrito_62', 'distrito_63', 'distrito_64', 'distrito_65', 'distrito

In [21]:
columns = [prices,m2,ascensor,exterior,planta,garaje,habs,
           construido_en,banos,calefacion_central,calefacion_individual,es_casa,orientacion_sur,
           orientacion_oeste,orientacion_este,orientacion_norte,buen_estado,obra_nueva,
           movilidad_reducida,balcon,armarios,terraza,trastero,jardin,piscina,aire,energy_class]

d = {}


pd.DataFrame( d )


TypeError: __init__() takes from 1 to 6 positional arguments but 8 were given

In [25]:
prices._

list

In [43]:
locals()

{'__name__': '__main__',
 '__doc__': 'Automatically created module for IPython interactive environment',
 '__package__': None,
 '__loader__': None,
 '__spec__': None,
 '__builtin__': <module 'builtins' (built-in)>,
 '__builtins__': <module 'builtins' (built-in)>,
 '_ih': ['',
  'import pymongo\n\n# Connection to Mongo DB\ntry:\n    conn=pymongo.MongoClient()\n    print("connected")\nexcept pymongo.errors.ConnectionFailure as e:\n    print ("Could not connect to MongoDB: %s" % e )\n\ndb = conn["idealista"]\ncollection = db["house_data"]\nurls = db["urls"]',
  'import pandas as pd\nimport math\nimport numpy as np\ndf = pd.DataFrame()',
  '# Exploring the data\n\ncollection.find_one()',
  '# price\n\ndef getPrice(doc,l):\n    price = doc["price"]\n    price = price.replace("€","").replace(".","")\n    price = price.strip()\n    try:\n        price = int(price)\n    except:\n        #print(price)\n        price = 0\n    l.append(price)\n    \ncursor = collection.find({},{"price":1})\nl = [